# Visualization and `pyrosetta.distributed.viewer`

*Warning*: This notebook uses `pyrosetta.distributed.viewer` code, which runs in `jupyter notebook` and might not run if you're using `jupyterlab`.

The `pyrosetta.distributed` Viewer quickly renders `.pdb` files, dynamically instantiating `Pose` objects if required for certain visualization modules (matching the name `viewer.set*`). So when adding
visualization modules to the Viewer or using presets, passing `Pose` or `PackedPose` objects to the Viewer is suggested for quicker rendering. If a `Pose` object or `list`, `tuple`, or `set` of `Pose`
objects are provided to the Viewer, the Viewer will dynamically update upon `Pose` conformational changes by calling the `view.show()` method or equivalently `view()`. The Viewer applies visualization modules in the same order they are added (from left to right), so layering different styles (and `ResidueSelectors`) on top of one another becomes possible. The user must have already initialized PyRosetta providing `.params` files for any ligands and non-canonical residues in the input `Pose`(s)/`PackedPose`(s)/`.pdb` file(s), otherwise `pyrosetta.distributed` automatically initializes PyRosetta with default command line options.

Throughout this notebook, different syntaxes for constructing visualizations are demonstrated to show the flexibility of the `pyrosetta.distributed.viewer` API, with hopes you find your favorite.

**If you are using Google Colab:** Currently, `pyrosetta.distributed.viewer` does **not** require the local machine's PyMOL. You can always dump any `Pose` object into a `.pdb` file and open that in PyMOL on your own computer.
```
pose.dump_pdb("output_file.pdb")
```

*Note:* This Jupyter notebook requires the PyRosetta distributed layer which is obtained by building PyRosetta with the `--serialization` flag or installing PyRosetta from the RosettaCommons conda channel (for more information, visit: http://www.pyrosetta.org/dow).

In [1]:
import glob
import logging
logging.basicConfig(level=logging.INFO)
import os
import pyrosetta
import pyrosetta.distributed
import pyrosetta.distributed.io as io
import pyrosetta.distributed.viewer as viewer
import sys

if 'google.colab' in sys.modules:
    !pip install pyrosettacolabsetup
    import pyrosettacolabsetup
    pyrosettacolabsetup.setup()
    print ("Notebook is set for PyRosetta use in Colab.  Have fun!")

### Available `viewer` objects:

In [2]:
viewer.__all__

['expand_notebook',
 'init',
 'presets',
 'setBackgroundColor',
 'setDisulfides',
 'setHydrogenBonds',
 'setHydrogens',
 'setStyle',
 'setSurface',
 'setZoom',
 'setZoomTo']

For example: `viewer.init()`

### Available `viewer.presets` objects:

In [3]:
viewer.presets.__all__

['coreBoundarySurface', 'ligandsAndMetals']

For example: `viewer.presets.coreBoundarySurface()`

### `viewer` objects contain docstrings as user documentation:

In [4]:
help(viewer.init)

Help on function init in module pyrosetta.distributed.viewer.core:

init(packed_and_poses_and_pdbs=None, window_size=None, modules=None, delay=None, continuous_update=None, *args, **kwargs)
    Initialize the Viewer object.
    
    Parameters
    ----------
    first : required
        `packed_and_poses_and_pdbs`
    
        `PackedPose`, `Pose`, or `str` of a valid path to a .pdb file, or a `list`, `set`, or `tuple` of these objects.
    
    second : optional
        `window_size`
    
        `list` or `tuple` of `int` or `float` values for the (width, height) dimensions of the displayed window screen size.
        Default: (1200, 800)
    
    third : optional
        `modules`
        
        `list` of instantiated visualization modules to run upon changing amongst `packed_and_poses_and_pdbs` objects
        with the slider, matching the namespace `pyrosetta.distributed.viewer.set*`
        Default: []
    
    fourth : optional
        `delay`
        
        `float` or `int`

### `viewer.presets` objects contain docstrings as brief descriptions of each preset visualization

In [13]:
help(viewer.presets.coreBoundarySurface)

Help on function coreBoundarySurface in module pyrosetta.distributed.viewer.presets:

coreBoundarySurface(packed_and_poses_and_pdbs=None, *args, **kwargs)
    Display core residues as 'blackCarbon' sticks, boundary residues as 'greyCarbon' sticks, and surface residues
    as 'whiteCarbon' sticks, with 'spectrum' cartoon representation, using the default arguments in
    `pyrosetta.rosetta.core.select.residue_selector.LayerSelector()` to select layers.
    
    @klimaj



In [14]:
help(viewer.presets.ligandsAndMetals)

Help on function ligandsAndMetals in module pyrosetta.distributed.viewer.presets:

ligandsAndMetals(packed_and_poses_and_pdbs=None, *args, **kwargs)
    Display residues with `ResidueProperty.LIGAND` as 'brownCarbon' sticks with opaque surface,
    and `ResidueProperty.METAL` as 'chainHetatm' spheres, with 'spectrum' cartoon representation,
    disulfide bonds, polar hydrogens, and dashed hydrogen bonds.
    
    @klimaj



**From previous section:**
Make sure you are in the right directory for accessing the `.pdb` files:

`cd google_drive/My\ Drive/student-notebooks/`

**Note**: `import pyrosetta.distributed.viewer` expands the Jupyter notebook cell width to fit your internet browser, and can be called anytime using `pyrosetta.distributed.viewer.expand_notebook()`

In [15]:
flags = """
-auto_setup_metals 1
-detect_disulf 1
"""
pyrosetta.distributed.init(flags)

INFO:pyrosetta.distributed:maybe_init performing pyrosetta initialization: {'extra_options': '-auto_setup_metals 1 -detect_disulf 1', 'silent': True}
INFO:pyrosetta.rosetta:Found rosetta database at: /mnt/home/klimaj/git/Rosetta/main/source/src/python/PyRosetta/src/pyrosetta/database; using it....
INFO:pyrosetta.rosetta:PyRosetta-4 2019 [Rosetta PyRosetta4.conda.linux.CentOS.python36.Release 2019.39+release.93456a567a8125cafdf7f8cb44400bc20b570d81 2019-09-26T14:24:44] retrieved from: http://www.pyrosetta.org
(C) Copyright Rosetta Commons Member Institutions. Created in JHU by Sergey Lyskov and PyRosetta Team.
INFO:rosetta:core.init: {0} Checking for fconfig files in pwd and ./rosetta/flags
INFO:rosetta:core.init: {0} Rosetta version: PyRosetta4.conda.linux.CentOS.python36.Release r233 2019.39+release.93456a5 93456a567a8125cafdf7f8cb44400bc20b570d81 http://www.pyrosetta.org 2019-09-26T14:24:44
INFO:rosetta:core.init: {0} command: PyRosetta -ex1 -ex2aro -auto_setup_metals 1 -detect_disul

Show basic line representation of `.pdb` file on disk:

>```
view = viewer.init("path/to/my.pdb")
view.show()
```

Change the `window_size` option of `viewer.init()` to fit your screen size, which should prevent the need to scroll to view your macromolecular objects.

Show basic line representation of `Pose` or `PackedPose` objects in memory:

In [39]:
pose = pyrosetta.io.pose_from_file("inputs/3EK4.pdb")

INFO:rosetta:core.import_pose.import_pose: {0} File 'inputs/3EK4.pdb' automatically determined to be of type PDB
INFO:rosetta:core.io.pose_from_sfr.PoseFromSFRBuilder: {0} CA 350 was added by a jump, with base residue 258
INFO:rosetta:core.io.pose_from_sfr.PoseFromSFRBuilder: {0} CA 351 was added by a jump, with base residue 300
INFO:rosetta:core.io.pose_from_sfr.PoseFromSFRBuilder: {0} CA 352 was added by a jump, with base residue 338
INFO:rosetta:core.conformation.Conformation: {0} [ WARNING ] missing heavyatom: OXT on residue pdb_CRO 164
INFO:rosetta:core.chemical.AtomICoor: {0} [ WARNING ] IcoorAtomID::atom_id(): Cannot get atom_id for POLYMER_LOWER of residue VAL 165.  Returning BOGUS ID instead.
INFO:rosetta:core.conformation.Residue: {0} [ WARNING ] missing an atom: 165  H   that depends on a nonexistent polymer connection!
INFO:rosetta:core.conformation.Residue: {0} [ WARNING ]  --> generating it using idealized coordinates.
INFO:rosetta:core.conformation.Conformation: {0} [ WA

In [40]:
view = viewer.init(pose, window_size=(800, 600))
view()

You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol

To show basic cartoon representation, add `viewer.setStyle()`:

In [41]:
view = viewer.init(pose, window_size=(800, 600)) + viewer.setStyle()
view()

You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol

To visualize ligands, non-conanical residues, metals, etc., `viewer.setStyle()` (and several other `viewer.set*` objects) optionally accept PyRosetta `ResidueSelector` objects. In the case of `inputs/3EK4.pdb` which is a $Ca^{2+}$-saturated GCaMP2 monomer, a ligand is a $Ca^{2+}$ ion and a non-canonical residue is the chromophore "CRO", both of which are aleady parameterized and available in the PyRosetta residue type set database. Therefore, we do not need to initialize PyRosetta with custom "CA" or "CRO" `.params` files. However, if one wishes to visualize ligands and non-canonical residues for which `.params` files are not available in the PyRosetta residue type set database, one must first initialize PyRosetta providing `.params` files for any ligands and non-canonical residues in the input `Pose`(s) or `PackedPose`(s):

> pyrosetta.init("-extra_res_fa /path/to/LIG.fa.params")

`pyrosetta.distributed.viewer` passes the `Pose`'s PDB numbering of selected residues to `py3dmol` for macromolecular rendering. Also, one may layer any visualization modules with any `ResidueSelectors` in the order they are summed (from left to right). In this case:

In [42]:
metals_selector = pyrosetta.rosetta.core.select.residue_selector.ResiduePropertySelector(
     pyrosetta.rosetta.core.chemical.ResidueProperty.METAL
)
ligands_selector = pyrosetta.rosetta.core.select.residue_selector.ResiduePropertySelector(
     pyrosetta.rosetta.core.chemical.ResidueProperty.LIGAND
)

view = viewer.init(pose, window_size=(800, 600)) \
    + viewer.setStyle() \
    + viewer.setStyle(residue_selector=ligands_selector, style="stick", colorscheme="magentaCarbon", radius=0.5) \
    + viewer.setStyle(residue_selector=metals_selector, style="sphere", colorscheme="chainHetatm", radius=1.5)

 1. `viewer.setStyle()` layers the cartoon backbone and stick side-chain representation by default
 2. `viewer.setStyle(residue_selector=ligands_selector, style="stick", colorscheme="magentaCarbon", radius=0.5)` layers any residue with the `LIGAND` property a 0.5 radius stick with magenta carbon atoms.
 3. `viewer.setStyle(residue_selector=metals_selector, style="sphere", colorscheme="chainHetatm", radius=1.5)` layers any residue with the `METAL` property a 1.5 radius sphere with the `py3dmol` color scheme "chainHetatm". 

In [43]:
view()

You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol

Show many `Pose`s in memory using the interactive slider widget:

In [44]:
poses = [pyrosetta.io.pose_from_sequence("TESTVIEWER" * i) for i in range(1, 10)]

In [45]:
view = viewer.init(poses, continuous_update=True)
view.add(viewer.setStyle(colorscheme="lightgreyCarbon"))
view.add(viewer.setHydrogenBonds(radius=0.1, dashed=False))
view()

interactive(children=(IntSlider(value=0, description='Decoys', max=8), Output()), _dom_classes=('widget-intera…

<function pyrosetta.distributed.viewer.core.Viewer.show.<locals>.view(i=0)>

Below, layer a `ResidueSelector` of residues with `ResidueProperty.POLAR`, then hydrogen atoms, hydrogen bonds, and disulfide bonds:

In [46]:
packed_pose = io.to_packed(pose) # Test the Viewer with a PackedPose object

In [47]:
polar_residue_selector = pyrosetta.rosetta.core.select.residue_selector.ResiduePropertySelector(
    pyrosetta.rosetta.core.chemical.ResidueProperty.POLAR
)
view = viewer.init(packed_pose)
view.add(viewer.setStyle(radius=0.1))
view.add(viewer.setStyle(residue_selector=polar_residue_selector, colorscheme="whiteCarbon", radius=0.25, label=False))
view.add(viewer.setHydrogens(color="white", polar_only=True, radius=0.1))
view.add(viewer.setHydrogenBonds(color="black"))
view.add(viewer.setDisulfides(radius=0.1))
view()

You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol

In [48]:
view = sum(
    [
        viewer.init(pose),
        viewer.setStyle(cartoon=False, style="sphere", radius=1.5, colorscheme="darkgreyCarbon"),
        viewer.setZoom(factor=0.95)
    ]
)
view()

You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol

In [49]:
pose = pyrosetta.io.pose_from_file("inputs/6MSR.pdb")

INFO:rosetta:core.import_pose.import_pose: {0} File 'inputs/6MSR.pdb' automatically determined to be of type PDB
INFO:rosetta:core.io.pose_from_sfr.PoseFromSFRBuilder: {0} [ WARNING ] discarding 3 atoms at position 1 in file inputs/6MSR.pdb. Best match rsd_type:  GLY:NtermProteinFull
INFO:rosetta:core.io.pose_from_sfr.PoseFromSFRBuilder: {0} [ WARNING ] discarding 3 atoms at position 134 in file inputs/6MSR.pdb. Best match rsd_type:  GLY:NtermProteinFull
INFO:rosetta:core.io.pose_from_sfr.PoseFromSFRBuilder: {0} [ WARNING ] discarding 3 atoms at position 257 in file inputs/6MSR.pdb. Best match rsd_type:  GLY:NtermProteinFull
INFO:rosetta:core.conformation.Conformation: {0} [ WARNING ] missing heavyatom:  CD  on residue GLU 3
INFO:rosetta:core.conformation.Conformation: {0} [ WARNING ] missing heavyatom:  OE1 on residue GLU 3
INFO:rosetta:core.conformation.Conformation: {0} [ WARNING ] missing heavyatom:  OE2 on residue GLU 3
INFO:rosetta:core.conformation.Conformation: {0} [ WARNING ] 

INFO:rosetta:core.conformation.Conformation: {0} [ WARNING ] missing heavyatom:  CE  on residue LYS:CtermProteinFull 152
INFO:rosetta:core.conformation.Conformation: {0} [ WARNING ] missing heavyatom:  NZ  on residue LYS:CtermProteinFull 152
INFO:rosetta:core.conformation.Conformation: {0} [ WARNING ] missing heavyatom:  CD  on residue ARG 159
INFO:rosetta:core.conformation.Conformation: {0} [ WARNING ] missing heavyatom:  NE  on residue ARG 159
INFO:rosetta:core.conformation.Conformation: {0} [ WARNING ] missing heavyatom:  CZ  on residue ARG 159
INFO:rosetta:core.conformation.Conformation: {0} [ WARNING ] missing heavyatom:  NH1 on residue ARG 159
INFO:rosetta:core.conformation.Conformation: {0} [ WARNING ] missing heavyatom:  NH2 on residue ARG 159
INFO:rosetta:core.conformation.Conformation: {0} [ WARNING ] missing heavyatom:  CD  on residue LYS 160
INFO:rosetta:core.conformation.Conformation: {0} [ WARNING ] missing heavyatom:  CE  on residue LYS 160
INFO:rosetta:core.conformation

INFO:rosetta:core.pack.pack_missing_sidechains: {0} packing residue number 182 because of missing atom number 6 atom name  OG
INFO:rosetta:core.pack.pack_missing_sidechains: {0} packing residue number 184 because of missing atom number 6 atom name  CG
INFO:rosetta:core.pack.pack_missing_sidechains: {0} packing residue number 185 because of missing atom number 6 atom name  CG
INFO:rosetta:core.pack.pack_missing_sidechains: {0} packing residue number 187 because of missing atom number 7 atom name  CD
INFO:rosetta:core.pack.pack_missing_sidechains: {0} packing residue number 188 because of missing atom number 6 atom name  CG
INFO:rosetta:core.pack.pack_missing_sidechains: {0} packing residue number 189 because of missing atom number 6 atom name  CG
INFO:rosetta:core.pack.pack_missing_sidechains: {0} packing residue number 228 because of missing atom number 8 atom name  CD
INFO:rosetta:core.pack.task: {0} Packer task: initialize from command line()
INFO:rosetta:core.scoring.ScoreFunctionFa

In [50]:
chA = pyrosetta.rosetta.core.select.residue_selector.ChainSelector("A")
chB = pyrosetta.rosetta.core.select.residue_selector.ChainSelector("B")
view = sum(
    [
        viewer.init(pose),
        viewer.setStyle(cartoon_color="lightgrey", radius=0.25),
        viewer.setSurface(residue_selector=chA, colorscheme="greenCarbon", opacity=0.65, surface_type="VDW"),
        viewer.setSurface(residue_selector=chB, color="blue", opacity=0.75, surface_type="SAS"),
        viewer.setDisulfides(radius=0.25),
        viewer.setZoom(factor=1.5)
    ]
)
view()

You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol

In [51]:
view.reinit() # Subtract all visualization modules previously added to the Viewer
view()

You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol

`viewer.setZoomTo()` can zoom into a PyRosetta `ResidueSelector`:

In [52]:
pose = pyrosetta.io.pose_from_file("inputs/1QCQ.pdb")

INFO:rosetta:core.import_pose.import_pose: {0} File 'inputs/1QCQ.pdb' automatically determined to be of type PDB
INFO:rosetta:core.util.metalloproteins_util: {0} Automatically setting covalent bonds between metal ions and metal-binding residues.
INFO:rosetta:core.util.metalloproteins_util: {0} Automatically setting up constraints between metal ions and metal-binding residues.


In [53]:
helix_selector = pyrosetta.rosetta.core.select.residue_selector.SecondaryStructureSelector("H")
sheet_selector = pyrosetta.rosetta.core.select.residue_selector.SecondaryStructureSelector("E")
loop_selector = pyrosetta.rosetta.core.select.residue_selector.SecondaryStructureSelector("L")

modules = [
    viewer.setBackgroundColor(color="black"),
    viewer.setStyle(residue_selector=helix_selector, cartoon_color="blue", label=False, radius=0),
    viewer.setStyle(residue_selector=sheet_selector, cartoon_color="red", label=False, radius=0),
    viewer.setStyle(residue_selector=loop_selector, cartoon_color="white", label=False, radius=0),
    viewer.setZoomTo(residue_selector=sheet_selector)
]

In [54]:
viewer.init(pose, window_size=(1200, 600), modules=modules).show()

You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol

View live trajectory:

In [32]:
pose = pyrosetta.io.pose_from_file("inputs/2FD7.pdb")

INFO:rosetta:core.import_pose.import_pose: {0} File 'inputs/2FD7.pdb' automatically determined to be of type PDB
INFO:rosetta:core.conformation.Conformation: {0} [ WARNING ] missing heavyatom:  CG1 on residue VAL 15
INFO:rosetta:core.conformation.Conformation: {0} [ WARNING ] missing heavyatom:  CG2 on residue VAL 15
INFO:rosetta:core.conformation.Conformation: {0} Found disulfide between residues 3 40
INFO:rosetta:core.conformation.Conformation: {0} current variant for 3 CYS
INFO:rosetta:core.conformation.Conformation: {0} current variant for 40 CYS
INFO:rosetta:core.conformation.Conformation: {0} current variant for 3 CYD
INFO:rosetta:core.conformation.Conformation: {0} current variant for 40 CYD
INFO:rosetta:core.conformation.Conformation: {0} Found disulfide between residues 4 32
INFO:rosetta:core.conformation.Conformation: {0} current variant for 4 CYS
INFO:rosetta:core.conformation.Conformation: {0} current variant for 32 CYS
INFO:rosetta:core.conformation.Conformation: {0} curre

In [33]:
view = viewer.init(pose, delay=0.15) \
    + viewer.setStyle(radius=0.1) \
    + viewer.setDisulfides(radius=0.1)
backrub = pyrosetta.rosetta.protocols.backrub.BackrubMover()
minimize = pyrosetta.rosetta.protocols.minimization_packing.MinMover()

INFO:rosetta:core.mm.MMBondAngleLibrary: {0} MM bond angle sets added fully assigned: 603; wildcard: 0 and 1 virtual parameter.


In [34]:
for _ in range(100):
    backrub.apply(pose)
    minimize.apply(pose)
    view.show()

You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol

Display preset custom viewers for routine visualizations:

In [35]:
pdbfiles = [os.path.join("inputs", f) for f in ["3EK4.pdb", "6MSR.pdb", "1QCQ.pdb", "2FD7.pdb"]]
poses = [pyrosetta.io.pose_from_file(p) for p in pdbfiles]

INFO:rosetta:core.import_pose.import_pose: {0} File 'inputs/3EK4.pdb' automatically determined to be of type PDB
INFO:rosetta:core.io.pose_from_sfr.PoseFromSFRBuilder: {0} CA 350 was added by a jump, with base residue 258
INFO:rosetta:core.io.pose_from_sfr.PoseFromSFRBuilder: {0} CA 351 was added by a jump, with base residue 300
INFO:rosetta:core.io.pose_from_sfr.PoseFromSFRBuilder: {0} CA 352 was added by a jump, with base residue 338
INFO:rosetta:core.conformation.Conformation: {0} [ WARNING ] missing heavyatom: OXT on residue pdb_CRO 164
INFO:rosetta:core.chemical.AtomICoor: {0} [ WARNING ] IcoorAtomID::atom_id(): Cannot get atom_id for POLYMER_LOWER of residue VAL 165.  Returning BOGUS ID instead.
INFO:rosetta:core.conformation.Residue: {0} [ WARNING ] missing an atom: 165  H   that depends on a nonexistent polymer connection!
INFO:rosetta:core.conformation.Residue: {0} [ WARNING ]  --> generating it using idealized coordinates.
INFO:rosetta:core.conformation.Conformation: {0} [ WA

INFO:rosetta:core.conformation.Conformation: {0} [ WARNING ] missing heavyatom:  CG  on residue LYS 35
INFO:rosetta:core.conformation.Conformation: {0} [ WARNING ] missing heavyatom:  CD  on residue LYS 35
INFO:rosetta:core.conformation.Conformation: {0} [ WARNING ] missing heavyatom:  CE  on residue LYS 35
INFO:rosetta:core.conformation.Conformation: {0} [ WARNING ] missing heavyatom:  NZ  on residue LYS 35
INFO:rosetta:core.conformation.Conformation: {0} [ WARNING ] missing heavyatom:  CG  on residue LYS 36
INFO:rosetta:core.conformation.Conformation: {0} [ WARNING ] missing heavyatom:  CD  on residue LYS 36
INFO:rosetta:core.conformation.Conformation: {0} [ WARNING ] missing heavyatom:  CE  on residue LYS 36
INFO:rosetta:core.conformation.Conformation: {0} [ WARNING ] missing heavyatom:  NZ  on residue LYS 36
INFO:rosetta:core.conformation.Conformation: {0} [ WARNING ] missing heavyatom:  CD  on residue ARG 48
INFO:rosetta:core.conformation.Conformation: {0} [ WARNING ] missing heav

INFO:rosetta:core.conformation.Conformation: {0} [ WARNING ] missing heavyatom:  OE1 on residue GLU 185
INFO:rosetta:core.conformation.Conformation: {0} [ WARNING ] missing heavyatom:  OE2 on residue GLU 185
INFO:rosetta:core.conformation.Conformation: {0} [ WARNING ] missing heavyatom:  CD  on residue LYS 187
INFO:rosetta:core.conformation.Conformation: {0} [ WARNING ] missing heavyatom:  CE  on residue LYS 187
INFO:rosetta:core.conformation.Conformation: {0} [ WARNING ] missing heavyatom:  NZ  on residue LYS 187
INFO:rosetta:core.conformation.Conformation: {0} [ WARNING ] missing heavyatom:  CG  on residue LYS 188
INFO:rosetta:core.conformation.Conformation: {0} [ WARNING ] missing heavyatom:  CD  on residue LYS 188
INFO:rosetta:core.conformation.Conformation: {0} [ WARNING ] missing heavyatom:  CE  on residue LYS 188
INFO:rosetta:core.conformation.Conformation: {0} [ WARNING ] missing heavyatom:  NZ  on residue LYS 188
INFO:rosetta:core.conformation.Conformation: {0} [ WARNING ] mis

INFO:rosetta:core.conformation.Conformation: {0} Found disulfide between residues 16 26
INFO:rosetta:core.conformation.Conformation: {0} current variant for 16 CYS
INFO:rosetta:core.conformation.Conformation: {0} current variant for 26 CYS
INFO:rosetta:core.conformation.Conformation: {0} current variant for 16 CYD
INFO:rosetta:core.conformation.Conformation: {0} current variant for 26 CYD
INFO:rosetta:core.pack.pack_missing_sidechains: {0} packing residue number 15 because of missing atom number 6 atom name  CG1
INFO:rosetta:core.pack.task: {0} Packer task: initialize from command line()
INFO:rosetta:core.scoring.ScoreFunctionFactory: {0} SCOREFUNCTION: ref2015
INFO:rosetta:core.scoring.ScoreFunctionFactory: {0} The -auto_setup_metals flag was used with no metalbinding_constraint weight set in the weights file.  Setting to 1.0.
INFO:rosetta:core.pack.pack_rotamers: {0} built 1 rotamers at 1 positions.
INFO:rosetta:core.pack.interaction_graph.interaction_graph_factory: {0} Instantiating

In [36]:
# Display preset custom viewers for routine visualizations:
viewer.presets.coreBoundarySurface(poses, window_size=(800, 600), continuous_update=True)

INFO:rosetta:core.select.residue_selector.LayerSelector: {0} Setting LayerSelector to use sidechain neighbors to determine burial.
INFO:rosetta:core.select.residue_selector.LayerSelector: {0} Set cutoffs for core and surface to 5.2 and 2, respectively, in LayerSelector.
INFO:rosetta:core.select.residue_selector.LayerSelector: {0} Setting core=true boundary=false surface=false in LayerSelector.
INFO:rosetta:core.select.residue_selector.LayerSelector: {0} Setting LayerSelector to use sidechain neighbors to determine burial.
INFO:rosetta:core.select.residue_selector.LayerSelector: {0} Set cutoffs for core and surface to 5.2 and 2, respectively, in LayerSelector.
INFO:rosetta:core.select.residue_selector.LayerSelector: {0} Setting core=false boundary=true surface=false in LayerSelector.
INFO:rosetta:core.select.residue_selector.LayerSelector: {0} Setting LayerSelector to use sidechain neighbors to determine burial.
INFO:rosetta:core.select.residue_selector.LayerSelector: {0} Set cutoffs fo

interactive(children=(IntSlider(value=0, description='Decoys', max=3), Output()), _dom_classes=('widget-intera…

<function pyrosetta.distributed.viewer.core.Viewer.show.<locals>.view(i=0)>

In [37]:
viewer.presets.ligandsAndMetals(poses, window_size=(800, 600), continuous_update=False)

interactive(children=(IntSlider(value=0, continuous_update=False, description='Decoys', max=3), Output()), _do…

<function pyrosetta.distributed.viewer.core.Viewer.show.<locals>.view(i=0)>

**For Developers**: contribute your custom preset visualizations to PyRosetta:

 1. Edit `~Rosetta/main/source/src/python/PyRosetta/src/pyrosetta/distributed/viewer/presets/\_\_init\_\_.py`
 2. Copy and modify the `templatePreset` function, renaming it to the name of your new preset Viewer (e.g. `myCustomPreset` in step #5).
 3. Add the name of your new preset Viewer to the `__all__` list.
 4. Merge Github pull request into `RosettaCommons/main`
 5. Example using it:
 ```
    import pyrosetta.distributed.viewer as viewer
    viewer.presets.myCustomPreset(poses)
 ```

In [38]:
def myCustomPreset(packed_and_poses_and_pdbs=None, *args, **kwargs):
    """
    Add a description of the preset Viewer here
    """
    # Add custrom ResidueSelectors
    metals_selector = pyrosetta.rosetta.core.select.residue_selector.ResiduePropertySelector(
         pyrosetta.rosetta.core.chemical.ResidueProperty.METAL
    )
    ligands_selector = pyrosetta.rosetta.core.select.residue_selector.ResiduePropertySelector(
         pyrosetta.rosetta.core.chemical.ResidueProperty.LIGAND
    )
    
    # Add custom Viewer commands
    view = viewer.init(packed_and_poses_and_pdbs=packed_and_poses_and_pdbs, *args, **kwargs) \
        + viewer.setBackgroundColor("white") \
        + viewer.setStyle(style="stick", colorscheme="lightgreyCarbon", radius=0.15) \
        + viewer.setStyle(residue_selector=ligands_selector, style="stick", colorscheme="brownCarbon", radius=0.5, label=True) \
        + viewer.setStyle(residue_selector=metals_selector, style="sphere", colorscheme="chainHetatm", radius=1.5, label=True) \
        + viewer.setHydrogenBonds() \
        + viewer.setDisulfides(radius=0.15) \
        + viewer.setHydrogens(color="white", radius=0.033, polar_only=True) \
        + viewer.setSurface(residue_selector=ligands_selector, surface_type="VDW", opacity=0.5, color="magenta") \
        + viewer.setSurface(residue_selector=metals_selector, surface_type="VDW", opacity=0.5, color="magenta") \
        + viewer.setZoomTo(residue_selector=ligands_selector)

    return view()

myCustomPreset(poses[0])

You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol

# Documentation for `pyrosetta.distributed.viewer` visualization modules

In [5]:
help(viewer.setBackgroundColor)

Help on class setBackgroundColor in module pyrosetta.distributed.viewer.modules:

class setBackgroundColor(builtins.object)
 |  Set Viewer background color with either Hexcode or standard colors.
 |  
 |  Parameters
 |  ----------
 |  first : optional
 |      `color`
 |  
 |      Hexcode literal (e.g. 0xffffffff) or `str` indicating a standard color (e.g. "black").
 |      Default: 0xffffffff
 |  
 |  Returns
 |  -------
 |  A Viewer instance.
 |  
 |  Methods defined here:
 |  
 |  __init__(self, color=4294967295)
 |      Initialize self.  See help(type(self)) for accurate signature.
 |  
 |  apply(self, viewer, pose, pdbstring)
 |  
 |  ----------------------------------------------------------------------
 |  Data descriptors defined here:
 |  
 |  __dict__
 |      dictionary for instance variables (if defined)
 |  
 |  __weakref__
 |      list of weak references to the object (if defined)



In [6]:
help(viewer.setDisulfides)

Help on class setDisulfides in module pyrosetta.distributed.viewer.modules:

class setDisulfides(builtins.object)
 |  Display disulfide bonds according to `pyrosetta.rosetta.core.conformation.is_disulfide_bond()`
 |  for all combinations of cysteine residues in each initialized `.pdb` file, `Pose` or `PackedPose` object.
 |  
 |  Parameters
 |  ----------
 |  first : optional
 |      `color`
 |  
 |      `str` indicating a standard color (e.g. "black").
 |      Default: "gold"
 |  
 |  second : optional
 |      `radius`
 |  
 |      `float` or `int` indicating the radius of the stick connecting the atoms participating in each disulfide bond.
 |      Default: 0.5
 |  
 |  Returns
 |  -------
 |  A Viewer instance.
 |  
 |  Methods defined here:
 |  
 |  __init__(self, color='gold', radius=0.5)
 |      Initialize self.  See help(type(self)) for accurate signature.
 |  
 |  apply(self, viewer, pose, pdbstring)
 |  
 |  ----------------------------------------------------------------------

In [7]:
help(viewer.setHydrogenBonds)

Help on class setHydrogenBonds in module pyrosetta.distributed.viewer.modules:

class setHydrogenBonds(builtins.object)
 |  Display hydrogen bonds according to `pyrosetta.rosetta.core.pose.Pose.get_hbonds()`
 |  in each initialized `.pdb` file, `Pose` or `PackedPose` object.
 |  
 |  Parameters
 |  ----------
 |  first : optional
 |      `color`
 |  
 |      `str` indicating a standard color (e.g. "yellow").
 |      Default: "black"
 |  
 |  second : optional
 |      `dashed`
 |  
 |      `True` or `False` to show hydrogen bonds as dashed lines.
 |      If `True`, then option `radius` must be `None`.
 |      If `False`, then option `radius` must be specified.
 |      Default: True
 |  
 |  third : optional
 |      `radius`
 |  
 |      `float` or `int` indicating the radius of the solid (non-dashed) stick connecting the atoms participating
 |      in each hydrogen bond. If set, this automatically sets the option `dashed` to `False`.
 |      Default: None
 |  
 |  Returns
 |  -------
 |

In [8]:
help(viewer.setHydrogens)

Help on class setHydrogens in module pyrosetta.distributed.viewer.modules:

class setHydrogens(builtins.object)
 |  Show all or only polar hydrogen atoms in each initialized `.pdb` file, `Pose` or `PackedPose` object.
 |  
 |  Parameters
 |  ----------
 |  first : optional
 |      `color`
 |  
 |      `str` indicating a standard color (e.g. "grey").
 |      Default: "white"
 |  
 |  second : optional
 |      `radius`
 |  
 |      `float` or `int` indicating the radius of the hydrogen atom stick represnetations.
 |      Default: 0.05
 |  
 |  third : optional
 |      `polar_only`
 |  
 |      `True` or `False`. `True` to show only polar hydrogen atoms, and `False` to show all hydrogen atoms.
 |      Default: False
 |  
 |  Returns
 |  -------
 |  A Viewer instance.
 |  
 |  Methods defined here:
 |  
 |  __init__(self, color='white', radius=0.05, polar_only=False)
 |      Initialize self.  See help(type(self)) for accurate signature.
 |  
 |  apply(self, viewer, pose, pdbstring)
 |  
 |

In [9]:
help(viewer.setStyle)

Help on class setStyle in module pyrosetta.distributed.viewer.modules:

class setStyle(builtins.object)
 |  Show and color cartoon, and/or show heavy atoms with provided style, color and radius for each initialized
 |  `.pdb` file, `Pose` or `PackedPose` object. If the `residue_selector` argument is provided, apply styles
 |  only to the selected residues. If the `command` argument is provided, override all other arguments and pass
 |  `py3Dmol.view.setStyle()` commands to the Viewer.
 |  
 |  Parameters
 |  ----------
 |  first : optional
 |      `residue_selector`
 |      
 |      An instance of `pyrosetta.rosetta.core.select.residue_selector.ResidueSelector` on which to apply the style(s).
 |      Default: None
 |  
 |  second : optional
 |      `cartoon`
 |      
 |      `True` or `False` to show cartoon representation.
 |      Default: True
 |  
 |  third : optional
 |      `cartoon_color`
 |      
 |      Hexcode literal (e.g. 0xAF10AB) or `str` indicating a standard color (e.g. 

In [10]:
help(viewer.setSurface)

Help on class setSurface in module pyrosetta.distributed.viewer.modules:

class setSurface(builtins.object)
 |  Show the specified surface for each initialized `.pdb` file, `Pose` or `PackedPose` object.
 |  
 |  Parameters
 |  ----------
 |  first : optional
 |      `residue_selector`
 |      
 |      An instance of `pyrosetta.rosetta.core.select.residue_selector.ResidueSelector` to select residues
 |      on which to apply the surface.
 |      Default: None
 |  
 |  second : optional
 |      `surface_type`
 |  
 |      `str` indicating surface type to be displayed. py3Dmol supports the following options:
 |          "VDW": Van der Waals surface
 |          "MS": Molecular surface
 |          "SES": Solvent excluded surface
 |          "SAS": Solvent accessible surface
 |      Default: "VDW"
 |  
 |  third : optional
 |      `opacity`
 |  
 |      `float` or `int` between 0 and 1 for opacity of the displayed surface.
 |      Default: 0.5
 |  
 |  fourth : optional
 |      `color`
 |  

In [11]:
help(viewer.setZoom)

Help on class setZoom in module pyrosetta.distributed.viewer.modules:

class setZoom(builtins.object)
 |  Set the zoom magnification factor of each initialized `.pdb` file, `Pose` or `PackedPose` object.
 |  Values >1 zoom in, and values <1 zoom out.
 |  
 |  Parameters
 |  ----------
 |  first : optional
 |      `factor`
 |  
 |      `float` or `int` indicating the zoom magnification factor.
 |      Default: 2
 |  
 |  Returns
 |  -------
 |  A Viewer instance.
 |  
 |  Methods defined here:
 |  
 |  __init__(self, factor=2)
 |      Initialize self.  See help(type(self)) for accurate signature.
 |  
 |  apply(self, viewer, pose, pdbstring)
 |  
 |  ----------------------------------------------------------------------
 |  Data descriptors defined here:
 |  
 |  __dict__
 |      dictionary for instance variables (if defined)
 |  
 |  __weakref__
 |      list of weak references to the object (if defined)



In [12]:
help(viewer.setZoomTo)

Help on class setZoomTo in module pyrosetta.distributed.viewer.modules:

class setZoomTo(builtins.object)
 |  Zoom to a `ResidueSelector` in each initialized `.pdb` file, `Pose` or `PackedPose` object.
 |  
 |  Parameters
 |  ----------
 |  first : optional
 |      `residue_selector`
 |  
 |      An instance of `pyrosetta.rosetta.core.select.residue_selector.ResidueSelector` into which to zoom.
 |      Default: None
 |  
 |  Returns
 |  -------
 |  A Viewer instance.
 |  
 |  Methods defined here:
 |  
 |  __init__(self, residue_selector=None)
 |      Initialize self.  See help(type(self)) for accurate signature.
 |  
 |  apply(self, viewer, pose, pdbstring)
 |  
 |  ----------------------------------------------------------------------
 |  Data descriptors defined here:
 |  
 |  __dict__
 |      dictionary for instance variables (if defined)
 |  
 |  __weakref__
 |      list of weak references to the object (if defined)

